In [1]:
#imports
import multiprocessing
import re
import requests, sys, json
from urllib.request import urlretrieve
from collections import Counter

In [2]:
with open('buchnera_anotation_not_precalc.tsv', 'r') as p, open('go-basic.obo', 'r') as r:
    info = p.readlines()
    descriptions = []
    for i in range(1, len(info)):
        l = info[i].split('\t')
        descriptions.append(l)
descriptions

[['sp|P57575|RL18_BUCAI',
  'd51f2eb45a7abd2c6a803322aa1e8d15',
  '122',
  'CDD',
  'cd00432',
  'Ribosomal_L18_L5e',
  '30',
  '120',
  '1.73843E-33',
  'T',
  '08-01-2024',
  '-',
  '-',
  '-',
  '-\n'],
 ['sp|P57575|RL18_BUCAI',
  'd51f2eb45a7abd2c6a803322aa1e8d15',
  '122',
  'Hamap',
  'MF_01337_B',
  '50S ribosomal protein L18 [rplR].',
  '7',
  '122',
  '24.638233',
  'T',
  '08-01-2024',
  'IPR004389',
  'Large ribosomal subunit protein uL18, bacterial-type',
  'GO:0003735(InterPro)|GO:0005840(InterPro)|GO:0006412(InterPro)',
  '-\n'],
 ['sp|P57575|RL18_BUCAI',
  'd51f2eb45a7abd2c6a803322aa1e8d15',
  '122',
  'SUPERFAMILY',
  'SSF53137',
  'Translational machinery components',
  '9',
  '120',
  '9.59E-47',
  'T',
  '08-01-2024',
  '-',
  '-',
  '-',
  '-\n'],
 ['sp|P57575|RL18_BUCAI',
  'd51f2eb45a7abd2c6a803322aa1e8d15',
  '122',
  'PANTHER',
  'PTHR12899',
  '39S RIBOSOMAL PROTEIN L18, MITOCHONDRIAL',
  '12',
  '122',
  '2.6E-23',
  'T',
  '08-01-2024',
  'IPR005484',
  'Larg

In [10]:
#Obteniendo un archivo con las relaciones de IPR a GO's
url = (
    'https://ftp.ebi.ac.uk/pub/databases/interpro/current_release/interpro2go'
)
filename = "interpro2go.txt"
path, headers = urlretrieve(url, filename)
for name, value in headers.items():
    print(name, value)

Date Mon, 15 Jan 2024 23:12:18 GMT
Server Apache
Last-Modified Wed, 08 Nov 2023 19:11:51 GMT
ETag "2f7bf3-609a8dc0e61df"
Accept-Ranges bytes
Content-Length 3111923
Access-Control-Allow-Origin *
Access-Control-Allow-Methods GET,OPTIONS
Access-Control-Allow-Headers Authorization,Origin,User-Agent,X-Requested-With,If-Modified-Since,Cache-Control,Content-Type,Range,Accept
Connection close


# Función empleada para descargar desde ftp los archivos requeridos

In [84]:
def get_archives(url, filename):
    
    path, headers = urlretrieve(url, filename)
    return path, headers

In [86]:
u = 'https://ftp.ebi.ac.uk/pub/databases/interpro/current_release/entry.list'
f = 'IPR_list.tsv'
get_archives(u, f)

('IPR_list.tsv', <http.client.HTTPMessage at 0x2326c5c1a00>)

# Formateo del archivo IPR_list.tsv.
En él, vienen los IPR ID correspondientes para Sitios activos, conservados, Dominios, Familias, Superfamilias, etc.

In [5]:
with open('IPR_list.tsv', 'r') as pr:
    info = pr.readlines()
    ac_type_name = [i.replace('\n', '').split('\t') for i in info[1:]]

In [6]:
ac_type_name

[['IPR000126',
  'Active_site',
  'Serine proteases, V8 family, serine active site'],
 ['IPR000138', 'Active_site', 'Hydroxymethylglutaryl-CoA lyase, active site'],
 ['IPR000169', 'Active_site', 'Cysteine peptidase, cysteine active site'],
 ['IPR000180', 'Active_site', 'Membrane dipeptidase, active site'],
 ['IPR000189', 'Active_site', 'Prokaryotic transglycosylase, active site'],
 ['IPR000590',
  'Active_site',
  'Hydroxymethylglutaryl-coenzyme A synthase, active site'],
 ['IPR001252', 'Active_site', 'Malate dehydrogenase, active site'],
 ['IPR001345',
  'Active_site',
  'Phosphoglycerate/bisphosphoglycerate mutase, active site'],
 ['IPR001497',
  'Active_site',
  'Methylated-DNA-[protein]-cysteine S-methyltransferase, active site'],
 ['IPR001555',
  'Active_site',
  'Phosphoribosylglycinamide formyltransferase, active site'],
 ['IPR001579',
  'Active_site',
  'Glycosyl hydrolases family 18 (GH18) active site'],
 ['IPR001586', 'Active_site', 'Beta-lactamase, class-C active site'],
 ['

In [16]:
#Formateando el archivo IPR a GO's
with open('interpro2go.txt', 'r') as r:
    info=r.readlines()
    ipr_gos = []
    for i in info[5:]:
        # infosplitted = i.replace('\n', '').replace.split('>')
        # infosplitted[1].replace(';', '\t').split('\t')
        # print(infosplitted)
        infosplitted = i.replace('\n', '').replace(' ', '>', 1).replace(';', '>').replace(' ', '').replace('InterPro:', '').split('>')
        ipr_gos.append(infosplitted)

In [17]:
ipr_gos

[['IPR000003', 'RetinoidXreceptor/HNF4', 'GO:DNAbinding', 'GO:0003677'],
 ['IPR000003',
  'RetinoidXreceptor/HNF4',
  'GO:nuclearsteroidreceptoractivity',
  'GO:0003707'],
 ['IPR000003', 'RetinoidXreceptor/HNF4', 'GO:zincionbinding', 'GO:0008270'],
 ['IPR000003',
  'RetinoidXreceptor/HNF4',
  'GO:regulationofDNA-templatedtranscription',
  'GO:0006355'],
 ['IPR000003', 'RetinoidXreceptor/HNF4', 'GO:nucleus', 'GO:0005634'],
 ['IPR000006',
  'Metallothionein,vertebrate',
  'GO:metalionbinding',
  'GO:0046872'],
 ['IPR000009',
  'Proteinphosphatase2AregulatorysubunitPR55',
  'GO:proteinphosphataseregulatoractivity',
  'GO:0019888'],
 ['IPR000009',
  'Proteinphosphatase2AregulatorysubunitPR55',
  'GO:proteinphosphatasetype2Acomplex',
  'GO:0000159'],
 ['IPR000010',
  'Cystatindomain',
  'GO:cysteine-typeendopeptidaseinhibitoractivity',
  'GO:0004869'],
 ['IPR000011',
  'Ubiquitin/SUMO-activatingenzymeE1-like',
  'GO:ubiquitin-likemodifieractivatingenzymeactivity',
  'GO:0008641'],
 ['IPR000

In [8]:
bases_de_datos = {}
c=0
filtrado_por_ipr= [i[3] for i in descriptions if i[11] != '-']
# len([i for i in filtrado_por_gos if i[3]=='PANTHER'])
filtrado_por_ipr

['Hamap',
 'PANTHER',
 'NCBIfam',
 'Pfam',
 'Pfam',
 'PANTHER',
 'CDD',
 'NCBIfam',
 'SMART',
 'Gene3D',
 'ProSiteProfiles',
 'Pfam',
 'Pfam',
 'PIRSF',
 'ProSitePatterns',
 'SUPERFAMILY',
 'SUPERFAMILY',
 'Pfam',
 'ProSiteProfiles',
 'SUPERFAMILY',
 'Gene3D',
 'SMART',
 'Gene3D',
 'Hamap',
 'NCBIfam',
 'PANTHER',
 'SUPERFAMILY',
 'ProSiteProfiles',
 'ProSitePatterns',
 'Pfam',
 'NCBIfam',
 'SMART',
 'Pfam',
 'Pfam',
 'Gene3D',
 'Pfam',
 'PANTHER',
 'SUPERFAMILY',
 'PIRSF',
 'SUPERFAMILY',
 'Pfam',
 'NCBIfam',
 'Pfam',
 'NCBIfam',
 'SUPERFAMILY',
 'PANTHER',
 'SUPERFAMILY',
 'NCBIfam',
 'ProSitePatterns',
 'Gene3D',
 'ProSitePatterns',
 'Pfam',
 'Gene3D',
 'SUPERFAMILY',
 'Hamap',
 'PANTHER',
 'Gene3D',
 'Pfam',
 'NCBIfam',
 'SUPERFAMILY',
 'PIRSF',
 'Pfam',
 'ProSitePatterns',
 'SUPERFAMILY',
 'NCBIfam',
 'PANTHER',
 'Hamap',
 'SUPERFAMILY',
 'NCBIfam',
 'PRINTS',
 'PRINTS',
 'PRINTS',
 'PRINTS',
 'PRINTS',
 'PRINTS',
 'PANTHER',
 'SUPERFAMILY',
 'Hamap',
 'Gene3D',
 'Pfam',
 'Gene3D'

In [6]:
from collections import Counter
bases = Counter(filtrado_por_ipr)

In [9]:
bases_per = {}
for i, j in bases.items():
    bases_per[i] = (j/len(filtrado_por_ipr))*100
bases_per

{'Hamap': 7.566037735849057,
 'PANTHER': 5.830188679245283,
 'NCBIfam': 9.056603773584905,
 'Pfam': 17.69811320754717,
 'CDD': 4.849056603773585,
 'SMART': 3.471698113207547,
 'Gene3D': 12.283018867924527,
 'ProSiteProfiles': 3.6415094339622645,
 'PIRSF': 2.69811320754717,
 'ProSitePatterns': 6.339622641509433,
 'SUPERFAMILY': 13.11320754716981,
 'PRINTS': 13.264150943396228,
 'SFLD': 0.18867924528301888}

In [10]:
#Definir keywords
keywords = ["DNA-binding", "Helix-turn-helix",
            "Helix-loop-helix", "zinc finger",
            "Leucine zipper", "Winged",
            "bHLH", "HTH", "Winged helix",
            "winged-helix", "helix turn helix",
            "HMG", "leucine-zipper", "zinc-finger",
            "Zn-finger", "Zinc finger", "IHF-like",
            "Sigma",
            "Homeodomain-like", "Homeodomain", "HemN-like",
            "3'DNA-binding domain", "(3'BD)",
            "alpha-hairpin", "transcription factor",
            "Regulator", "Regulatory", "Histon-like",
            "Nucleic acid-binding", "Winged helix",
            "winged-helix", "Homeobox-like", "Homeobox", "HTH", "FIS-type",
            "nucleotide-binding domain", "DNA binding"]

# Fltrado de los IPR Ids segun los keywords

In [11]:
## filtro de los IPR-TYPE-NAME 
ipr_filtred = [resultado for resultado in ac_type_name
                        if any(keyword.lower() in resultado[2].lower() for keyword in keywords)]
ipr_filtred

[['IPR020003',
  'Active_site',
  'ATPase, alpha/beta subunit, nucleotide-binding domain, active site'],
 ['IPR015887',
  'Binding_site',
  'DNA glycosylase/AP lyase, zinc finger domain, DNA-binding site'],
 ['IPR025662',
  'Binding_site',
  'Sigma-54 interaction domain, ATP-binding site 1'],
 ['IPR025943',
  'Binding_site',
  'Sigma-54 interaction domain, ATP-binding site 2'],
 ['IPR000047', 'Conserved_site', 'Helix-turn-helix motif'],
 ['IPR000637', 'Conserved_site', 'HMG-I/HMG-Y, DNA-binding, conserved site'],
 ['IPR000838',
  'Conserved_site',
  'RNA polymerase sigma factor 70, ECF, conserved site'],
 ['IPR001562', 'Conserved_site', 'Zinc finger, Btk motif'],
 ['IPR001827',
  'Conserved_site',
  'Homeobox protein, antennapedia type, conserved site'],
 ['IPR003956',
  'Conserved_site',
  'Transcription factor, NFYB/HAP3, conserved site'],
 ['IPR005486',
  'Conserved_site',
  'Glucokinase regulatory protein, conserved site'],
 ['IPR013734', 'Conserved_site', 'Transcription factor Nrm

In [22]:
with open('IPR_filtros.tsv', 'w') as out:
    ipr_filtred_list = []
    for i in ipr_filtred:
        a = [i[0], i[1], i[2]]
        ipr_filtred_list.append(a)

In [25]:
len(ipr_filtred_list), len(ipr_filtred)

(1891, 1891)

In [20]:
put_regulatory_gos = []
for i in ipr_filtred:
    for j in ipr_gos:
        if i[0] == j[0]:
            put_regulatory_gos.append(j[-1])


In [26]:
put_regulatory_gos = list(set(put_regulatory_gos))
put_regulatory_gos

['GO:0043087',
 'GO:0006406',
 'GO:0048578',
 'GO:0005509',
 'GO:0045892',
 'GO:0035303',
 'GO:0043546',
 'GO:0006959',
 'GO:0006289',
 'GO:0060962',
 'GO:0043565',
 'GO:0045895',
 'GO:0008988',
 'GO:0005667',
 'GO:2000031',
 'GO:0048830',
 'GO:0006281',
 'GO:0046782',
 'GO:0003678',
 'GO:0003713',
 'GO:0031167',
 'GO:0019670',
 'GO:0035658',
 'GO:0005981',
 'GO:0000226',
 'GO:0032559',
 'GO:0000164',
 'GO:0006935',
 'GO:0005524',
 'GO:0021778',
 'GO:0070824',
 'GO:1990195',
 'GO:0006391',
 'GO:0000166',
 'GO:0032933',
 'GO:0006383',
 'GO:0005198',
 'GO:0090729',
 'GO:2000142',
 'GO:0019210',
 'GO:0042981',
 'GO:0044781',
 'GO:0002244',
 'GO:0004864',
 'GO:0004222',
 'GO:0008324',
 'GO:0006952',
 'GO:0005672',
 'GO:0016151',
 'GO:0008289',
 'GO:0008603',
 'GO:0060090',
 'GO:0003906',
 'GO:0006468',
 'GO:0051091',
 'GO:0005096',
 'GO:0045944',
 'GO:0005694',
 'GO:0006275',
 'GO:0016575',
 'GO:0016192',
 'GO:0016567',
 'GO:0003691',
 'GO:0045152',
 'GO:0016514',
 'GO:0009739',
 'GO:00320

In [28]:
#filtro de la salida de IPRScan con los IPRS acs_type_name de INTERPRO con la descriptción de dominios
output_filtred = []
for i in ipr_filtred: #recorre la lista de IPRS, dominio y name
    for j in descriptions: #recorre la salida de IPRScan
        if i[0] == j[11]: #i[0] corresponde a IPR filtrado con keywords, j[11] es el IPR de la salida de IPRScan
            f = [j[0], i[0], i[2], i[1], j[13]]
            output_filtred.append(f)
output_filtred

[['sp|P57122|ATPA_BUCAI',
  'IPR020003',
  'ATPase, alpha/beta subunit, nucleotide-binding domain, active site',
  'Active_site',
  'GO:0005524(InterPro)'],
 ['sp|P57124|ATPB_BUCAI',
  'IPR020003',
  'ATPase, alpha/beta subunit, nucleotide-binding domain, active site',
  'Active_site',
  'GO:0005524(InterPro)'],
 ['sp|P57294|DKSA_BUCAI',
  'IPR020458',
  'Zinc finger, DksA/TraR C4-type conserved site',
  'Conserved_site',
  '-'],
 ['sp|P57394|IHFB_BUCAI',
  'IPR020816',
  'Histone-like DNA-binding protein, conserved site',
  'Conserved_site',
  'GO:0003677(InterPro)'],
 ['sp|P57144|DBH_BUCAI',
  'IPR020816',
  'Histone-like DNA-binding protein, conserved site',
  'Conserved_site',
  'GO:0003677(InterPro)'],
 ['sp|P57231|IHFA_BUCAI',
  'IPR020816',
  'Histone-like DNA-binding protein, conserved site',
  'Conserved_site',
  'GO:0003677(InterPro)'],
 ['sp|P57652|RHO_BUCAI',
  'IPR000194',
  'ATPase, F1/V1/A1 complex, alpha/beta subunit, nucleotide-binding domain',
  'Domain',
  'GO:000552

In [29]:
len(output_filtred)

210

In [52]:
output_filtred[0][-1] 

'GO:0005524(InterPro)'

In [53]:
###procesamiento de los GOS en cada lista de output filtred
put_regulatory_gos

{'GO:0000062',
 'GO:0000105',
 'GO:0000122',
 'GO:0000123',
 'GO:0000124',
 'GO:0000126',
 'GO:0000127',
 'GO:0000139',
 'GO:0000150',
 'GO:0000155',
 'GO:0000156',
 'GO:0000159',
 'GO:0000160',
 'GO:0000164',
 'GO:0000166',
 'GO:0000226',
 'GO:0000281',
 'GO:0000309',
 'GO:0000381',
 'GO:0000398',
 'GO:0000439',
 'GO:0000502',
 'GO:0000723',
 'GO:0000724',
 'GO:0000774',
 'GO:0000781',
 'GO:0000785',
 'GO:0000921',
 'GO:0000976',
 'GO:0000977',
 'GO:0000978',
 'GO:0000981',
 'GO:0000995',
 'GO:0001070',
 'GO:0001216',
 'GO:0001217',
 'GO:0001227',
 'GO:0001228',
 'GO:0001514',
 'GO:0001671',
 'GO:0001817',
 'GO:0001932',
 'GO:0001965',
 'GO:0002218',
 'GO:0002244',
 'GO:0003407',
 'GO:0003676',
 'GO:0003677',
 'GO:0003678',
 'GO:0003684',
 'GO:0003690',
 'GO:0003691',
 'GO:0003697',
 'GO:0003700',
 'GO:0003712',
 'GO:0003713',
 'GO:0003714',
 'GO:0003723',
 'GO:0003727',
 'GO:0003746',
 'GO:0003824',
 'GO:0003887',
 'GO:0003896',
 'GO:0003899',
 'GO:0003906',
 'GO:0003911',
 'GO:00039

In [31]:
len([i[0] for i in output_filtred])

210

In [32]:
#PENDIENTE DE OPTIMIZACIÓN
#GO'S RELACIONADOS A REGULACIÓN
reg_gos = ['GO:0141096',
 'GO:0001216',
 'GO:0001228',
 'GO:0016987',
 'GO:0001227',
 'GO:0106250',
 'GO:0141097',
 'GO:0000981',
 'GO:0098531',
 'GO:0004879',
 'GO:0003700',
 'GO:0001217',
 'GO:0043380',
 'GO:0043382',
 'GO:0043381',
 'GO:0051091',
 'GO:0032793',
 'GO:2000825',
 'GO:0007228',
 'GO:0051092',
 'GO:1904743',
 'GO:0043392',
 'GO:1902596',
 'GO:0061774',
 'GO:0061781',
 'GO:1903026',
 'GO:1905768',
 'GO:1905497',
 'GO:2000678',
 'GO:1901840',
 'GO:1905494',
 'GO:1904797',
 'GO:0007253',
 'GO:0032088',
 'GO:0032792',
 'GO:0043433',
 'GO:0042994',
 'GO:0003677']
put_regulatory_gos.extend(reg_gos)

In [43]:
put_regulatory_gos = set(put_regulatory_gos)
len(put_regulatory_gos), len(output_filtred)

(466, 210)

In [58]:
##asignación de score de confiabilidad
# 1 GO NO relacionado a regulación
# 2 NO TIENE GO
# 3 GO relacionado a regulación
one = [item for item in output_filtred if item[-1] != '-' and not any(go in item[-1] for go in put_regulatory_gos)]
two = [i for i in output_filtred if i[-1] == '-']
three = [item for item in output_filtred if item[-1] != '-' and any(go in item[-1] for go in put_regulatory_gos)]
# for i in output_filtred:
#     for j in put_regulatory_gos:
#         if j in i[-1]:
#             three.append(i)

#         else:
#             # one.append(i)


In [59]:
len(one), len(two), len(three)


(0, 91, 119)

In [170]:
patron = re.compile(r'sp\|([A-Za-z0-9]+)\|')
info_protes = [re.search(patron, r[0]).group(1) for r in three]
info_protes=set(info_protes)

In [171]:
#documentacion: https://www.uniprot.org/help/api
WEBSITE_API = WEBSITE_API = "https://rest.uniprot.org/"
#documentación: https://ww.ebi.ac.uk/proteins/api/doc/
PROTEINS_API = "https://www.ebi.ac.uk/proteins/api"
#funcion que ayuda a descargar datos desde uniprot
def get_url(url, **kwargs):
    response = requests.get(url, **kwargs)

    if not response.ok:
        print(response.text)
        response.raise_for_status()
        sys.exit()
    return response

In [173]:
pIDs = set([i[0] for i in info_protes])
pIDs

{'O', 'P'}

In [174]:
info_protes

{'O05385',
 'O32464',
 'O32465',
 'P57116',
 'P57122',
 'P57124',
 'P57144',
 'P57161',
 'P57163',
 'P57164',
 'P57172',
 'P57178',
 'P57220',
 'P57231',
 'P57294',
 'P57354',
 'P57371',
 'P57375',
 'P57394',
 'P57407',
 'P57451',
 'P57453',
 'P57459',
 'P57480',
 'P57484',
 'P57546',
 'P57548',
 'P57555',
 'P57610',
 'P57615',
 'P57628',
 'P57652',
 'P57659',
 'P57660',
 'P63237'}

In [179]:
for i in info_protes:
    try:
        req = get_url(f"{WEBSITE_API}/uniprotkb/{i}")
        api_data = req.json()
        gene = api_data['genes'][0]['geneName']['value']
        name = api_data['proteinDescription']['recommendedName']['fullName']['value']

        print(i, gene, name)
    except:
        print(i)
        # print('No puedo acceder a geneName, no existe, solo tengo {i}')

P57615 hemW Heme chaperone HemW
P57459 nusA Transcription termination/antitermination protein NusA
P57172 ligA DNA ligase
P63237 cspE Cold shock-like protein CspE
P57652 rho Transcription termination factor Rho
P57161 secB Protein-export protein SecB
P57164 dnaG DNA primase
P57555 htpG Chaperone protein HtpG
P57124 atpD ATP synthase subunit beta
P57484 csrA Translational regulator CsrA
P57231 ihfA Integration host factor subunit alpha
P57546 tig Trigger factor
P57178 fliI Flagellum-specific ATP synthase
P57660 hscA Chaperone protein HscA
P57294 dksA RNA polymerase-binding transcription factor DksA
P57628 rnr Ribonuclease R
P57453 deaD ATP-dependent RNA helicase DeaD
P57163 rpoD RNA polymerase sigma factor RpoD
P57394 ihfB Integration host factor subunit beta
P57480 fis DNA-binding protein Fis
P57220 priA Primosomal protein N'
P57375 hisS Histidine--tRNA ligase
P57659 hscB Co-chaperone protein HscB
P57144 hup DNA-binding protein HU
P57407 cspC Cold shock-like protein CspC
P57116 hslU AT

In [11]:
#open archives in other directory


P57633 mutL
P57484 csrA
P57164 dnaG
P57240 surA
P57458 infB
P57220 priA
P57660 hscA
P57480 fis
P57400 infA
P57459 nusA
P57308 ftsZ
P57286 sodA
P57354 rnb
P25750 groEL
P57401 aspS
P57395 rpsA
P57555 htpG
P57418 flgA
P57135 dnaT
P57178 fliI
P57550 ppiD
P57454 pnp
P57451 pyrI
P57512 lysS
P57161 secB
P57554
P57375 hisS
O32465 dnaJ
P57640 ibp
P57628 rnr
P57548 clpX
P25749 groES
P57249 ileS
P57503 cysJ
O05385 rpoH
P63237 cspE
P57122 atpA
P57588 rplB
P57610 ssb
P57172 ligA
O32464 dnaK
P57546 tig
P57128 dnaA
P57441 asnS
P57116 hslU
P57652 rho
P57132 mnmE
P57182 fliM
P57394 ihfB
P57516 miaB
P57545
P57183 fliN
P57641 fpr
P57578 rpsN
P57615 hemW
P57429 rne
P57231 ihfA
P57659 hscB
P57126 gyrB
P57133 efp
P57453 deaD
P57144 hup
P57582 rpsQ
P57465
P57124 atpD
P57163 rpoD
P57200 hisG
P57320 ilvH
P57371 topA
P57294 dksA
P57230 pheT
Q9ZEY8 leuA
P57360 hns
P57407 cspC
P57595 rpsL
